# Extract FASTA sequences for Genes

This script loads a .csv or .txt file of gene names.  
These are converted to ensembl gene and transcript IDs .  
The ensembl canonical transcript is selected before  the genes corresponding transcript coding sequences are loaded as FASTA sequences.  
These are saved as a FASTA file.

> Databases and MARTS are all specified for the mouse genome

## 1. Prepare your workspace
### Install Dependencies

In [1]:
# BiocManager::install("EnsDb.Mmusculus.v79")
# BiocManager::install("TxDb.Mmusculus.UCSC.mm10.knownGene")
# BiocManager::install("biomaRt")
# BiocManager::install("org.Mm.eg.db")
# BiocManager::install("ChIPpeakAnno")
# BiocManager::install("Biostrings")
# BiocManager::install("GenomicFeatures")
# BiocManager::install("AnnotationHub")
# BiocManager::install("tidysq")
# install.packages("ape")
# install.packages("seqinr")
# install.packages("rentrez") # set API key
# install.packages("AnnotationBustR") # https://cran.r-project.org/web/packages/AnnotationBustR/vignettes/AnnotationBustR-vignette.html
# install.packages("janitor") # to find duplicates w. dplyr
# install.packages("read.gb")
# BiocManager::install("customProDB") # to extract fasta
# install.packages("RMariaDB")
# install.packages("rtracklayer")
# install.packages("data.table")

### Load Dependencies

In [2]:
# library(janitor)
library(EnsDb.Mmusculus.v79)
library(TxDb.Mmusculus.UCSC.mm10.knownGene)
library(biomaRt)
library(org.Mm.eg.db)
library(ChIPpeakAnno)
library(Biostrings)
library(GenomicFeatures)
library(tidysq)
library(dplyr)
library(stringr)
library(tidyr)
# library(ape) #this is a general R-package for phylogenetics and comparative methods
# library(seqinr) #this is an specialized package for nucleotide sequence management
library(rentrez)
library(AnnotationBustR)
library(read.gb)
library(customProDB)
library(RMariaDB)
library(rtracklayer)
library(data.table)
library(AnnotationHub)

Loading required package: ensembldb

Warning message:
“package ‘ensembldb’ was built under R version 4.1.2”
Loading required package: BiocGenerics


Attaching package: ‘BiocGenerics’


The following objects are masked from ‘package:stats’:

    IQR, mad, sd, var, xtabs


The following objects are masked from ‘package:base’:

    anyDuplicated, append, as.data.frame, basename, cbind, colnames,
    dirname, do.call, duplicated, eval, evalq, Filter, Find, get, grep,
    grepl, intersect, is.unsorted, lapply, Map, mapply, match, mget,
    order, paste, pmax, pmax.int, pmin, pmin.int, Position, rank,
    rbind, Reduce, rownames, sapply, setdiff, sort, table, tapply,
    union, unique, unsplit, which.max, which.min


Loading required package: GenomicRanges

Warning message:
“package ‘GenomicRanges’ was built under R version 4.1.2”
Loading required package: stats4

Loading required package: S4Vectors

Warning message:
“package ‘S4Vectors’ was built under R version 4.1.2”

Attaching package: ‘

In [3]:
set_entrez_key("0cc4b6c802bd36a1dc0970a9b244d3de1a09")

# Identify correct Ensembl database if required
ensembl <- useMart(host="https://uswest.ensembl.org",
                   biomart="ENSEMBL_MART_ENSEMBL", dataset="mmusculus_gene_ensembl",
                   port = 443)
# listDatasets(ensembl)
# datasets <- listDatasets(ensembl)

### Functions

The following functions promt the user for file name entry (.csv or .txt), read respective csv or txt file, and write FASTA files.

In [41]:
# Function to promt user for file name entry
enterFileName <- function(){ 
  filename <- readline(prompt="Enter file name: ")
  return(filename)
}

# read CSV file function
readCSV <- function() {
  file <- read.csv(filename, header = TRUE)
  return(file)
}

# read txt file function
readTXT <- function() {
  file <- read.table(filename, header = TRUE)
  return(file)
}

# Write FASTA file that takes a data.frame that has a first column as 
# transcript ID and second as FASTA seq
writeFasta <- function(data, filename){
  fastaLines = c()
  for (rowNum in 1:nrow(data)){
    fastaLines = c(fastaLines, as.character(paste(">", data[rowNum,1], sep = "")))
    fastaLines = c(fastaLines,as.character(data[rowNum,2]))
  }
  fileConn<-file(filename)
  writeLines(fastaLines, fileConn)
  close(fileConn)
}

### Find Filenames and load gene list
First we load the working directory.

In [5]:
getwd()

[1] "/Users/ines/Documents/4.PostDoc/Probe_design/Methods"

Depending on where your file containing your target gene list is, you can now set your working directory.

In [6]:
setwd("~/Documents/4.PostDoc/Probe_design/Probe_dealer_trial1/Data")

> Now prompt the user to enter the file name!!

In [7]:
# trialfile here is probe_test_list.txt
filename <- enterFileName()

Enter file name (.csv or .txt): probe_test_list.txt


Now load the file if it is a .txt or .csv file.

In [11]:
if (grepl("csv", filename, ignore.case ="TRUE") == TRUE) {
  df = readCSV()
  print("This is a .csv file")
  print(df)
} else {
  print("This is not a .csv file")
}

if (grepl("txt", filename, ignore.case ="TRUE")  == TRUE) {
  df = readTXT()
  print("This is a .txt file")
  print(df)
} else {
  print("This is not a .txt file")
}

[1] "This is not a .csv file"
[1] "This is a .txt file"
       cluster    gene
1      Atrophy  Trim63
2      Atrophy     Cpe
3      Atrophy    Elk4
4      Atrophy   Dupd1
5      Atrophy  Fbxo32
6      Atrophy   Nabp1
7      Atrophy    Hpgd
8      Atrophy   Foxo1
9      Atrophy   Ect2l
10     Atrophy  Ptpn14
11     Atrophy   Ampd3
12     Atrophy    Mdm2
13     Atrophy  Galnt7
14 Denervation    Dlg2
15 Denervation   Dclk1
16 Denervation   Map1b
17 Denervation Ccdc141
18 Denervation Gm45159
19 Denervation   Runx1
20 Denervation   Tnnt2
21 Denervation Gm11149
22 Denervation   Tead4
23 Denervation   Kcnn3
24 Denervation  Ppfia4
25 Denervation   Scn5a
26 Denervation   Ncam1
27 Denervation  Ankrd1


## 2. Manipulate Data
### 2.1 Convert data from Gene Symbol to ensembl Gene and Transcript ID

In [14]:
# Create a list of only gene IDs
geneSymbols <-  df$gene

# search available attributes in your mart
# searchAttributes(mart = ensembl, pattern = "transcript_")
geneID <- getBM(filters= "external_gene_name", 
                attributes= c("ensembl_gene_id", "external_gene_name", 
                              "ensembl_transcript_id", "transcript_is_canonical",
                              "transcript_count",
                              "transcript_start", "transcript_end"),
                geneSymbols, mart = ensembl)

In [15]:
print(geneID)

       ensembl_gene_id external_gene_name ensembl_transcript_id
1   ENSMUSG00000020184               Mdm2    ENSMUST00000020408
2   ENSMUSG00000020184               Mdm2    ENSMUST00000105263
3   ENSMUSG00000020184               Mdm2    ENSMUST00000155285
4   ENSMUSG00000020184               Mdm2    ENSMUST00000132277
5   ENSMUSG00000020184               Mdm2    ENSMUST00000131627
6   ENSMUSG00000020184               Mdm2    ENSMUST00000137102
7   ENSMUSG00000020184               Mdm2    ENSMUST00000126022
8   ENSMUSG00000020184               Mdm2    ENSMUST00000147823
9   ENSMUSG00000020184               Mdm2    ENSMUST00000151725
10  ENSMUSG00000052727              Map1b    ENSMUST00000064762
11  ENSMUSG00000052727              Map1b    ENSMUST00000224702
12  ENSMUSG00000052727              Map1b    ENSMUST00000223693
13  ENSMUSG00000052727              Map1b    ENSMUST00000223725
14  ENSMUSG00000052727              Map1b    ENSMUST00000224605
15  ENSMUSG00000052727              Map1

As you can see each gene has several transcripts. We only want one transcript per gene for further analysis at this point since ProbeDealer can only deal with a limited number of inputs.  

### 2.2 Keep canonical transcript copy
The ensembl canonical transcript is the most conserved and highly expressed transcript.  
Other transcripts might be non-protein coding, or result in proteins that undergo nonsense mediated decay.

In [16]:
geneID_can  <- geneID %>%
            dplyr::filter(transcript_is_canonical == 1)

Display the difference in transcript number between all transcript IDs belonging to our list of genes and canonical transcripts.   There should be one canonical transcript per gene.

In [25]:
paste("There are", nrow(geneID), "transcript IDs")
paste("There are", nrow(geneID_can), "canonical transcript IDs")

print(geneID_can)

[1] "There are 175 transcript IDs"

[1] "There are 27 canonical transcript IDs"

      ensembl_gene_id external_gene_name ensembl_transcript_id
1  ENSMUSG00000020184               Mdm2    ENSMUST00000020408
2  ENSMUSG00000052727              Map1b    ENSMUST00000064762
3  ENSMUSG00000039542              Ncam1    ENSMUST00000194252
4  ENSMUSG00000079564            Gm11149    ENSMUST00000216483
5  ENSMUSG00000022952              Runx1    ENSMUST00000023673
6  ENSMUSG00000024803             Ankrd1    ENSMUST00000237142
7  ENSMUSG00000026107              Nabp1    ENSMUST00000027279
8  ENSMUSG00000031613               Hpgd    ENSMUST00000034026
9  ENSMUSG00000031608             Galnt7    ENSMUST00000034021
10 ENSMUSG00000037852                Cpe    ENSMUST00000048967
11 ENSMUSG00000030353              Tead4    ENSMUST00000006311
12 ENSMUSG00000044167              Foxo1    ENSMUST00000053764
13 ENSMUSG00000028834             Trim63    ENSMUST00000105875
14 ENSMUSG00000063821              Dupd1    ENSMUST00000073870
15 ENSMUSG00000027797              Dclk1    ENSMUST0000

### 2.3 Get transcript sequences, 5' UTR, CDS and 3'UTR >> cDNA sequence
gene_exon = a single splice variant that is coding or noncoding   
coding transcript is comprised of 5'UTR, 3'UTR ends + CDS

In [26]:
seqID1 <- getSequence(id = geneID_can$ensembl_transcript_id, 
                     type="ensembl_transcript_id",
                     seqType="cdna", 
                     mart=ensembl)

In [34]:
# Table is right aligned in Jupyter - SCROLL to right to see details
View(seqID1)

cdna                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            

Merge metadata about 27 canonical transcripts and their sequences.

In [36]:
seqs <- merge(geneID_can, seqID1, by="ensembl_transcript_id")

In [38]:
paste("There are", nrow(seqs), "canonical transcript ID sequences")
View(seqs)

[1] "There are 27 canonical transcript ID sequences"

ensembl_transcript_id ensembl_gene_id    external_gene_name
1  ENSMUST00000000811    ENSMUSG00000000794 Kcnn3             
2  ENSMUST00000006311    ENSMUSG00000030353 Tead4             
3  ENSMUST00000020408    ENSMUSG00000020184 Mdm2              
4  ENSMUST00000022986    ENSMUSG00000022358 Fbxo32            
5  ENSMUST00000023673    ENSMUSG00000022952 Runx1             
6  ENSMUST00000027279    ENSMUSG00000026107 Nabp1             
7  ENSMUST00000034021    ENSMUSG00000031608 Galnt7            
8  ENSMUST00000034026    ENSMUSG00000031613 Hpgd              
9  ENSMUST00000048967    ENSMUSG00000037852 Cpe               
10 ENSMUST00000053764    ENSMUSG00000044167 Foxo1             
11 ENSMUST00000054237    ENSMUSG00000027797 Dclk1             
12 ENSMUST00000064762    ENSMUSG00000052727 Map1b             
13 ENSMUST00000073870    ENSMUSG00000063821 Dupd1             
14 ENSMUST00000086556    ENSMUSG00000026436 Elk4              
15 ENSMUST00000097442    ENSMUSG00000026604 Ptpn14            
16 ENSMUST00000105875    ENSMUSG00000028834 Trim63            
17 ENSMUST00000117911    ENSMUSG00000032511 Scn5a             
18 ENSMUST00000164114    ENSMUSG00000044033 Ccdc141           
19 ENSMUST00000168515    ENSMUSG00000026458 Ppfia4            
20 ENSMUST00000188028    ENSMUSG00000026414 Tnnt2             
21 ENSMUST00000194252    ENSMUSG00000039542 Ncam1             
22 ENSMUST00000208630    ENSMUSG00000109125 Gm45159           
23 ENSMUST00000208948    ENSMUSG00000071392 Ect2l             
24 ENSMUST00000213373    ENSMUSG00000005686 Ampd3             
25 ENSMUST00000216483    ENSMUSG00000079564 Gm11149           
26 ENSMUST00000231777    ENSMUSG00000052572 Dlg2              
27 ENSMUST00000237142    ENSMUSG00000024803 Ankrd1            
   transcript_is_canonical transcript_count transcript_start transcript_end
1  1                        2                89427471         89575068     
2  1                        5               128204106        128277776     
3  1                        9               117524780        117546663     
4  1                        1                58039275         58078328     
5  1                        7                92398354         92623037     
6  1                       10                51508647         51517558     
7  1                        4                57976862         58106065     
8  1                        1                56747620         56774078     
9  1                        4                65045576         65146088     
10 1                        1                52175757         52260642     
11 1                       15                55149947         55446485     
12 1                        6                99557954         99653048     
13 1                        2                21726605         21764644     
14 1                        7               131935345        131954186     
15 1                        6               189460465        189608892     
16 1                        4               134042431        134056940     
17 1                        4               119312476        119408082     
18 1                       11                76840339         77000961     
19 1                        6               134224521        134260666     
20 1                       15               135764092        135779998     
21 1                        7                49413448         49479849     
22 1                        1                90536280         90589260     
23 1                        7                18004770         18077101     
24 1                        8               110368118        110411126     
25 1                        4                49429588         49479325     
26 1                       22                90126439         92098455     
27 1                        6                36089365         36097499     
   cdna                                                                                                        

### 2.4 Are any of our genes are missing?

In [39]:
# identify missing gene names in our sequences set from the original geneID input
missing <- dplyr::filter(geneID,! external_gene_name %in% seqs$external_gene_name)
print(missing)

[1] ensembl_gene_id         external_gene_name      ensembl_transcript_id  
[4] transcript_is_canonical transcript_count        transcript_start       
[7] transcript_end         
<0 rows> (or 0-length row.names)


## 3. Write FASTA from data frame

### 3.1 Create data frame containing only the columns we want

In [43]:
data <- dplyr::select(seqs, -c(2:7))

> Prompt the user to enter the file name under which you want to save the file ending in .fasta!!
> Ideally save fasta file on same date you download your ensembl identifiers and add date to filename.  
This allows you to go back to particular gene/transcript model in Ensembl, even if an update occurred.

In [44]:
save_filename <- enterFileName()

Enter file name: trial_fasta.fasta


Finally save the Fasta file.

In [45]:
writeFasta(data, save_filename)

### 3.2 Open saved FASTA file
Test if saving of the file worked by opening the saved fasta file.

In [55]:
dna <- readDNAStringSet("trial_fasta.fasta")

In [56]:
View(dna)

DNAStringSet object of length 27:
     width seq                                              names               
 [1]  2884 ATTGAGCCAGCGAGGAGTGAAGC...CCAAAGTGGGGTGTGCTGAGCA ENSMUST00000000811
 [2]  3076 GCGAGGCGCGCCCCACCCCGGCG...TCAATAAATATGCATTGGTACT ENSMUST00000006311
 [3]  3099 GTTCTCTCCGCGGACGGTAGGGG...TGAAAGAGATTTGTCTTACACA ENSMUST00000020408
 [4]  6976 GGGGCGGGCTAAGAGCAGGCGGC...TAAATGTTTTTCCTACAACACA ENSMUST00000022986
 [5]  5861 AAGTCACGTGATTGGCAAGAGCC...TAAACAATTTGACAAGCACCTA ENSMUST00000023673
 ...   ... ...
[23]  2862 ATGTCACTTGGGAGCCTTCCCCT...AATCAGAAGCAGTATGAAGTAA ENSMUST00000208948
[24]  3337 ATGGCCCTGCCCTCCGAATCCGC...ACTAGGTAGAATTTTTAAGTCT ENSMUST00000213373
[25]  1275 ATAAAGCAGCCAGGATGGTCCAA...AAGAAGCAAAAACCTGAACCTG ENSMUST00000216483
[26]  7801 ACAGAAGAAAAATAGGAAAGTGA...TTTTTACTTTATAGCAAAATTA ENSMUST00000231777
[27]  2020 TACGTGGGATGACTCGCATTGCT...TAATAAATGCAAACTAATTCTC ENSMUST00000237142